# Field Detection using Semi-supervised SimCLR

In [17]:
import math
import matplotlib.pyplot as plt

import tensorflow as tf
tf.compat.v1.enable_eager_execution()
tf.get_logger().setLevel('ERROR')
tf.autograph.set_verbosity(1)
import tensorflow_datasets as tfds
from tensorflow import keras
from tensorflow.keras import layers



import pandas as pd
import numpy as np

import folium
import h3

In [18]:
from pathlib import Path
parquet_dir_training = Path('D:\hexes_with_pixels_s2\hex_index_L3=832a89fffffffff')
parquet_dir_validation = Path('D:\hexes_with_pixels_s2\hex_index_L3=832a89fffffffff')

In [19]:
df = pd.concat(
            pd.read_parquet(parquet_file)
            for parquet_file in parquet_dir_training.glob('*.parquet')
         )

display(df.head(5))
print(df.shape)

start_date                          end_date  \
0  2020-07-11T19:25:31.600000+00:00  2021-07-18T22:12:40.268000+00:00   
1  2020-07-11T19:25:31.600000+00:00  2021-07-18T22:12:40.268000+00:00   
2  2020-07-11T19:25:31.600000+00:00  2021-07-18T22:12:40.268000+00:00   
3  2020-07-11T19:25:31.600000+00:00  2021-07-18T22:12:40.268000+00:00   
4  2020-07-11T19:25:31.600000+00:00  2021-07-18T22:12:40.268000+00:00   

                              FIELD_OPERATION_GUID  \
0  07571e4f-0822-4803-aa14-c0cd079e414c 2020-11-08   
1  07571e4f-0822-4803-aa14-c0cd079e414c 2020-11-08   
2  07571e4f-0822-4803-aa14-c0cd079e414c 2020-11-08   
3  07571e4f-0822-4803-aa14-c0cd079e414c 2020-11-08   
4  07571e4f-0822-4803-aa14-c0cd079e414c 2020-11-08   

                                            scene_id              hex  \
0  S2A_MSIL2A_20200712T155911_N0214_R097_T17SQA_2...  8c2a891134001ff   
1  S2A_MSIL2A_20200712T155911_N0214_R097_T17SQA_2...  8c2a891134003ff   
2  S2A_MSIL2A_20200712T155911_N0214_R097_T17SQA_2...  8c2a891134005ff   
3  S2A_MSIL2A_20200712T155911_N0214_R097_T17SQA_2...  8c2a891134007ff   
4  S2A_MSIL2A_20200712T155911_N0214_R097_T17SQA_2...  8c2a891134009ff   

   SCL_val s2_tile    B01     B02     B03     B04     B05     B06     B07  \
0        4   17SQA  733.0  1005.0  1648.0  1626.0  2284.0  4004.0  4304.0   
1        4   17SQA  733.0   893.0  1566.0  1484.0  1953.0  3775.0  4208.0   
2        4   17SQA  714.0   469.0   911.0   664.0  1527.0  3296.0  3777.0   
3        4   17SQA  714.0   469.0   911.0   664.0  1527.0  3296.0  3777.0   
4        4   17SQA  733.0   937.0  1550.0  1522.0  2450.0  4127.0  4493.0   

      B08     B8A     B09     B11     B12  
0  4352.0  4589.0  4563.0  3291.0  2215.0  
1  4464.0  4457.0  4563.0  3076.0  1952.0  
2  3946.0  4145.0  4273.0  2715.0  1561.0  
3  4052.0  4145.0  4273.0  2715.0  1561.0  
4  4368.0  4633.0  4563.0  3493.0  2380.0

(123663, 19)


In [20]:
center = h3.h3_to_geo_boundary(h=df.iloc[0]['hex'],geo_json=True)

df = df.drop_duplicates(subset='hex', keep="first")

m = folium.Map(location=(center[0][1], center[0][0]),
                tiles = 'https://server.arcgisonline.com/ArcGIS/rest/services/World_Imagery/MapServer/tile/{z}/{y}/{x}',
                attr = 'Esri',
                name = 'Esri Satellite',
                zoom_start=16,
                overlay = False,
                control = True)

for index, row in df.iterrows():
    geometry = { "type" : "Polygon", "coordinates": [h3.h3_to_geo_boundary(h=row['hex'],geo_json=True)]}
    geo_j = folium.GeoJson(data=geometry, style_function=lambda x: {'fillColor': 'orange', 'color': 'green', 'weight': 0.5})
    folium.Popup(str(row['hex'])).add_to(geo_j)
    geo_j.add_to(m)

m

In [21]:
positive_samples = ['8c2a89113412bff', '8c2a891134069ff', '8c2a8911340cbff', '8c2a891acbb5dff', '8c2a891acba3dff', 
                    '8c2a891aa918bff', '8c2a891a85969ff']

negative_samples = ['8c2a891134ad3ff', '8c2a891a8c515ff', '8c2a891a8c509ff', '8c2a891a8c55bff', '8c2a891ae2d19ff', 
                    '8c2a891a86eb7ff', '8c2a891a82a67ff', '8c2a891134ae3ff', '8c2a891a86ccbff', '8c2a891a86ea5ff',
                    '8c2a891a861a1ff', '8c2a891aa9a8bff']

In [25]:
image_size = 12
image_channels = 1
width = 128
temperature = 0.1

steps_per_epoch = 20
AUTOTUNE = tf.data.AUTOTUNE
shuffle_buffer = 50
input_shape = (12,1)
width = 256
num_epochs = 100

temperature = 0.1
queue_size = 10000
contrastive_augmentation = {"min_area": 0.25, "brightness": 1, "jitter": 0.2}
classification_augmentation = {"min_area": 0.75, "brightness": 1, "jitter": 0.1}

In [26]:
def prepare_dataset():

    df = pd.concat(
            pd.read_parquet(parquet_file)
            for parquet_file in parquet_dir_training.glob('*.parquet')
         )
    
    df['y'] = np.where(np.isin(df['hex'],positive_samples), 1, -1)
    df['y'] = np.where(df['hex'].isin(negative_samples), 0, df['y'])
    
    print('Positive labeled samples:', sum(df.y==1))
    print('Negative labeled samples:', sum(df.y==0))
    print('Unlabeled labeled samples:', sum(df.y==-1))
    
    df_labeled = df[df.y != -1]
    df_unlabeled = df[df.y == -1]
    
    df_labeled = df_labeled[['B01','B02','B03','B04','B05','B06','B07','B08','B8A','B09','B11','B12', 'y']].astype('int')
    df_unlabeled = df_unlabeled[['B01','B02','B03','B04','B05','B06','B07','B08','B8A','B09','B11','B12', 'y']].astype('int')
    
    df_labeled_X_array = df_labeled.loc[:,df_labeled.columns != 'y']
    
    df_unlabeled_X_array = df_unlabeled.loc[:,df_unlabeled.columns != 'y']
    
    unlabeled_train_images = df_unlabeled.shape[0]
    labeled_train_images = df_labeled.shape[0]
    
    unlabeled_batch_size = unlabeled_train_images // steps_per_epoch
    labeled_batch_size = labeled_train_images // steps_per_epoch
    batch_size = unlabeled_batch_size + labeled_batch_size
    

    unlabeled_train_dataset = tf.data.Dataset\
        .from_tensor_slices((df_unlabeled_X_array, 
                            df_unlabeled.loc[:,df_unlabeled.columns == 'y'].values.T[0]))\
        .shuffle(50)\
        .batch(50, drop_remainder=True)
    
    labeled_train_dataset = tf.data.Dataset\
        .from_tensor_slices((df_labeled_X_array,
                             df_labeled.loc[:,df_labeled.columns == 'y'].values.T[0]))\
        .shuffle(50)\
        .batch(50, drop_remainder=True)
    
    test_dataset = tf.data.Dataset\
        .from_tensor_slices((df_labeled_X_array,
                             df_labeled.loc[:,df_labeled.columns == 'y'].values.T[0]))\
        .batch(50)\
        .prefetch(buffer_size=tf.data.AUTOTUNE)
    
   
    train_dataset = tf.data.Dataset.zip(
        (unlabeled_train_dataset,labeled_train_dataset)
    ).prefetch(buffer_size=AUTOTUNE)

    return batch_size, train_dataset, labeled_train_dataset, test_dataset

    
    
batch_size, train_dataset, labeled_train_dataset, test_dataset = prepare_dataset()

Positive labeled samples: 633
Negative labeled samples: 672
Unlabeled labeled samples: 122358


In [27]:
# Distorts the color distibutions of images
class RandomColorAffine(layers.Layer):
    def __init__(self, brightness=0, jitter=0, **kwargs):
        super().__init__(**kwargs)

        self.brightness = brightness
        self.jitter = jitter

    def get_config(self):
        config = super().get_config()
        config.update({"brightness": self.brightness, "jitter": self.jitter})
        return config

    def call(self, images, training=True):
        if training:
            batch_size = tf.shape(images)[0]

            # Same for all colors
            brightness_scales = 1 + tf.random.uniform(
                (batch_size, 1), minval=-self.brightness, maxval=self.brightness
            )
            # Different for all colors
            jitter_matrices = tf.random.uniform(
                (batch_size, 1), minval=-self.jitter, maxval=self.jitter
            )

            color_transforms = (
                tf.eye(1, batch_shape=[batch_size, 1]) * brightness_scales
                + jitter_matrices
            )
            images = tf.clip_by_value(tf.matmul(images, color_transforms), 0, 1)
        return images

# Define the encoder architecture
def get_encoder():
    return keras.Sequential(
        [
            keras.Input(shape=(image_size, image_channels)),
            layers.Conv1D(width, kernel_size=1, strides=2, activation="relu"),
            layers.Conv1D(width, kernel_size=1, strides=2, activation="relu"),
            layers.Conv1D(width, kernel_size=1, strides=2, activation="relu"),
            layers.Conv1D(width, kernel_size=1, strides=2, activation="relu"),
            layers.Flatten(),
            layers.Dense(width, activation="relu"),
        ],
        name="encoder",
    )

# Image augmentation module
def get_augmenter(min_area, brightness, jitter):
    zoom_factor = 1.0 - math.sqrt(min_area)
    return keras.Sequential(
        [
            keras.Input(shape=(image_size, image_size, image_channels)),
            layers.Rescaling(1 / 255),
            #layers.RandomFlip("horizontal"),
            #layers.RandomTranslation(zoom_factor / 2, zoom_factor / 2),
            #layers.RandomZoom((-zoom_factor, 0.0), (-zoom_factor, 0.0)),
            #RandomColorAffine(brightness, jitter),
        ]
    )


def visualize_augmentations(num_images):
    # Sample a batch from a dataset
    images = next(iter(train_dataset))[0][0][:num_images]
    # Apply augmentations
    augmented_images = zip(
        images,
        #get_augmenter(**classification_augmentation)(images),
        #get_augmenter(**contrastive_augmentation)(images),
        #get_augmenter(**contrastive_augmentation)(images),
    )
    row_titles = [
        "Original:",
        "Weakly augmented:",
        "Strongly augmented:",
        "Strongly augmented:",
    ]
    plt.figure(figsize=(num_images * 2.2, 4 * 2.2), dpi=100)
    for column, image_row in enumerate(augmented_images):
        for row, image in enumerate(image_row):
            plt.subplot(4, num_images, row * num_images + column + 1)
            plt.imshow(image)
            if column == 0:
                plt.title(row_titles[row], loc="left")
            plt.axis("off")
    plt.tight_layout()


#visualize_augmentations(num_images=8)

In [24]:
# Baseline supervised training with random initialization
baseline_model = keras.Sequential(
    [
        keras.Input(shape=(image_size, image_channels)),
        get_augmenter(**classification_augmentation),
        get_encoder(),
        layers.Dense(2),
    ],
    name="baseline_model",
)

baseline_model.compile(
    optimizer=keras.optimizers.Adam(),
    loss=keras.losses.SparseCategoricalCrossentropy(from_logits=True),
    metrics=[keras.metrics.SparseCategoricalAccuracy(name="acc")],
)

baseline_history = baseline_model.fit(
    labeled_train_dataset, epochs=num_epochs , validation_data=test_dataset
)

print(
    "Maximal validation accuracy: {:.2f}%".format(
        max(baseline_history.history["val_acc"]) * 100
    )
)

Epoch 1/100
26/26 [==============================] - 1s 20ms/step - loss: 0.6817 - acc: 0.5831 - val_loss: 0.6485 - val_acc: 0.7410
Epoch 2/100
26/26 [==============================] - 0s 6ms/step - loss: 0.6475 - acc: 0.6846 - val_loss: 0.6097 - val_acc: 0.7709
Epoch 3/100
26/26 [==============================] - 0s 6ms/step - loss: 0.6297 - acc: 0.6915 - val_loss: 0.5585 - val_acc: 0.7824
Epoch 4/100
26/26 [==============================] - 0s 6ms/step - loss: 0.5639 - acc: 0.7354 - val_loss: 0.5183 - val_acc: 0.7801
Epoch 5/100
26/26 [==============================] - 0s 6ms/step - loss: 0.5500 - acc: 0.7631 - val_loss: 0.5072 - val_acc: 0.7893
Epoch 6/100
26/26 [==============================] - 0s 6ms/step - loss: 0.5253 - acc: 0.7731 - val_loss: 0.4994 - val_acc: 0.7862
Epoch 7/100
26/26 [==============================] - 0s 5ms/step - loss: 0.5365 - acc: 0.7723 - val_loss: 0.5078 - val_acc: 0.7724
Epoch 8/100
26/26 [==============================] - 0s 6ms/step - loss: 0.5168 - 

26/26 [==============================] - 0s 7ms/step - loss: 0.4549 - acc: 0.7815 - val_loss: 0.4405 - val_acc: 0.7847
Epoch 64/100
26/26 [==============================] - 0s 7ms/step - loss: 0.4519 - acc: 0.7792 - val_loss: 0.4404 - val_acc: 0.7854
Epoch 65/100
26/26 [==============================] - 0s 6ms/step - loss: 0.4546 - acc: 0.7823 - val_loss: 0.4416 - val_acc: 0.7862
Epoch 66/100
26/26 [==============================] - 0s 7ms/step - loss: 0.4539 - acc: 0.7800 - val_loss: 0.4408 - val_acc: 0.7862
Epoch 67/100
26/26 [==============================] - 0s 6ms/step - loss: 0.4526 - acc: 0.7854 - val_loss: 0.4404 - val_acc: 0.7854
Epoch 68/100
26/26 [==============================] - 0s 6ms/step - loss: 0.4521 - acc: 0.7831 - val_loss: 0.4409 - val_acc: 0.7854
Epoch 69/100
26/26 [==============================] - 0s 6ms/step - loss: 0.4516 - acc: 0.7808 - val_loss: 0.4403 - val_acc: 0.7847
Epoch 70/100
26/26 [==============================] - 0s 6ms/step - loss: 0.4543 - acc: 0

In [10]:
print(baseline_history)


In [28]:
# Define the contrastive model with model-subclassing
class ContrastiveModel(keras.Model):
    def __init__(self):
        super().__init__()

        self.temperature = temperature
        self.contrastive_augmenter = get_augmenter(**contrastive_augmentation)
        self.classification_augmenter = get_augmenter(**classification_augmentation)
        self.encoder = get_encoder()
        # Non-linear MLP as projection head
        self.projection_head = keras.Sequential(
            [
                keras.Input(shape=(width,)),
                layers.Dense(width, activation="relu"),
                layers.Dense(width),
            ],
            name="projection_head",
        )
        # Single dense layer for linear probing
        self.linear_probe = keras.Sequential(
            [layers.Input(shape=(width,)), layers.Dense(2)], name="linear_probe"
        )

        self.encoder.summary()
        self.projection_head.summary()
        self.linear_probe.summary()

    def compile(self, contrastive_optimizer, probe_optimizer, **kwargs):
        super().compile(**kwargs)

        self.contrastive_optimizer = contrastive_optimizer
        self.probe_optimizer = probe_optimizer

        # self.contrastive_loss will be defined as a method
        self.probe_loss = keras.losses.SparseCategoricalCrossentropy(from_logits=True)

        self.contrastive_loss_tracker = keras.metrics.Mean(name="c_loss")
        self.contrastive_accuracy = keras.metrics.SparseCategoricalAccuracy(
            name="c_acc"
        )
        self.probe_loss_tracker = keras.metrics.Mean(name="p_loss")
        self.probe_accuracy = keras.metrics.SparseCategoricalAccuracy(name="p_acc")

    @property
    def metrics(self):
        return [
            self.contrastive_loss_tracker,
            self.contrastive_accuracy,
            self.probe_loss_tracker,
            self.probe_accuracy,
        ]

    def contrastive_loss(self, projections_1, projections_2):
        # InfoNCE loss (information noise-contrastive estimation)
        # NT-Xent loss (normalized temperature-scaled cross entropy)

        # Cosine similarity: the dot product of the l2-normalized feature vectors
        projections_1 = tf.math.l2_normalize(projections_1, axis=1)
        projections_2 = tf.math.l2_normalize(projections_2, axis=1)
        similarities = (
            tf.matmul(projections_1, projections_2, transpose_b=True) / self.temperature
        )

        # The similarity between the representations of two augmented views of the
        # same image should be higher than their similarity with other views
        batch_size = tf.shape(projections_1)[0]
        contrastive_labels = tf.range(batch_size)
        self.contrastive_accuracy.update_state(contrastive_labels, similarities)
        self.contrastive_accuracy.update_state(contrastive_labels, tf.transpose(similarities))

        # The temperature-scaled similarities are used as logits for cross-entropy
        # a symmetrized version of the loss is used here
        loss_1_2 = keras.losses.sparse_categorical_crossentropy(
            contrastive_labels, similarities, from_logits=True
        )
        loss_2_1 = keras.losses.sparse_categorical_crossentropy(
            contrastive_labels, tf.transpose(similarities), from_logits=True
        )
        return (loss_1_2 + loss_2_1) / 2
    
    @tf.function
    def train_step(self, data):
        (unlabeled_images, _), (labeled_images, labels) = data

        # Both labeled and unlabeled images are used, without labels
        images = tf.concat((unlabeled_images, labeled_images), axis=0)
        # Each image is augmented twice, differently
        #augmented_images_1 = self.contrastive_augmenter(images, training=True)
        #augmented_images_2 = self.contrastive_augmenter(images, training=True)
        
        print(images)
        augmented_images_1 = images
        augmented_images_2 = images
        
        print('train!!!!')
        print(data)
        
        
        with tf.GradientTape() as tape:
            features_1 = self.encoder(augmented_images_1, training=True)
            features_2 = self.encoder(augmented_images_2, training=True)
            
            print(features_1)
            print(features_2)
            
            
            #tf.print(features_1)
            # The representations are passed through a projection mlp
            projections_1 = self.projection_head(features_1, training=True)
            projections_2 = self.projection_head(features_2, training=True)
            contrastive_loss = self.contrastive_loss(projections_1, projections_2)
        gradients = tape.gradient(
            contrastive_loss,
            self.encoder.trainable_weights + self.projection_head.trainable_weights,
        )
        self.contrastive_optimizer.apply_gradients(
            zip(
                gradients,
                self.encoder.trainable_weights + self.projection_head.trainable_weights,
            )
        )
        self.contrastive_loss_tracker.update_state(contrastive_loss)

        # Labels are only used in evalutation for an on-the-fly logistic regression
        preprocessed_images = self.classification_augmenter(
            labeled_images, training=True
        )
        with tf.GradientTape() as tape:
            # the encoder is used in inference mode here to avoid regularization
            # and updating the batch normalization paramers if they are used
            features = self.encoder(preprocessed_images, training=False)
            class_logits = self.linear_probe(features, training=True)
            probe_loss = self.probe_loss(labels, class_logits)
        gradients = tape.gradient(probe_loss, self.linear_probe.trainable_weights)
        self.probe_optimizer.apply_gradients(
            zip(gradients, self.linear_probe.trainable_weights)
        )
        self.probe_loss_tracker.update_state(probe_loss)
        self.probe_accuracy.update_state(labels, class_logits)

        return {m.name: m.result() for m in self.metrics}

    def test_step(self, data):
        labeled_images, labels = data

        # For testing the components are used with a training=False flag
        preprocessed_images = self.classification_augmenter(
            labeled_images, training=False
        )
        features = self.encoder(preprocessed_images, training=False)
        class_logits = self.linear_probe(features, training=False)
        probe_loss = self.probe_loss(labels, class_logits)
        self.probe_loss_tracker.update_state(probe_loss)
        self.probe_accuracy.update_state(labels, class_logits)

        # Only the probe metrics are logged at test time
        return {m.name: m.result() for m in self.metrics[2:]}
    
# Contrastive pretraining
pretraining_model = ContrastiveModel()
pretraining_model.compile(
    contrastive_optimizer=keras.optimizers.Adam(),
    probe_optimizer=keras.optimizers.Adam(),
)

pretraining_history = pretraining_model.fit(
    train_dataset, epochs=num_epochs, validation_data=test_dataset
)
print(
    "Maximal validation accuracy: {:.2f}%".format(
        max(pretraining_history.history["val_p_acc"]) * 100
    )
)

Model: "encoder"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 conv1d_16 (Conv1D)          (None, 6, 12)             24        
                                                                 
 conv1d_17 (Conv1D)          (None, 3, 12)             156       
                                                                 
 conv1d_18 (Conv1D)          (None, 2, 12)             156       
                                                                 
 conv1d_19 (Conv1D)          (None, 1, 12)             156       
                                                                 
 flatten_4 (Flatten)         (None, 12)                0         
                                                                 
 dense_12 (Dense)            (None, 12)                156       
                                                                 
Total params: 648
Trainable params: 648
Non-trainable param

Epoch 30/100
26/26 [==============================] - 0s 3ms/step - c_loss: 2.7200 - c_acc: 0.6767 - p_loss: 0.6813 - p_acc: 0.7546 - val_p_loss: 0.6797 - val_p_acc: 0.7709
Epoch 31/100
26/26 [==============================] - 0s 4ms/step - c_loss: 2.7870 - c_acc: 0.6727 - p_loss: 0.6800 - p_acc: 0.7538 - val_p_loss: 0.6782 - val_p_acc: 0.7709
Epoch 32/100
26/26 [==============================] - 0s 3ms/step - c_loss: 2.8464 - c_acc: 0.6677 - p_loss: 0.6789 - p_acc: 0.7477 - val_p_loss: 0.6776 - val_p_acc: 0.7402
Epoch 33/100
26/26 [==============================] - 0s 4ms/step - c_loss: 2.9330 - c_acc: 0.6710 - p_loss: 0.6781 - p_acc: 0.7415 - val_p_loss: 0.6762 - val_p_acc: 0.7525
Epoch 34/100
26/26 [==============================] - 0s 4ms/step - c_loss: 2.8713 - c_acc: 0.6777 - p_loss: 0.6762 - p_acc: 0.7585 - val_p_loss: 0.6741 - val_p_acc: 0.7739
Epoch 35/100
26/26 [==============================] - 0s 4ms/step - c_loss: 2.7911 - c_acc: 0.6812 - p_loss: 0.6751 - p_acc: 0.7592 - v

26/26 [==============================] - 0s 4ms/step - c_loss: 2.4717 - c_acc: 0.6658 - p_loss: 0.6490 - p_acc: 0.7692 - val_p_loss: 0.6444 - val_p_acc: 0.7724
Epoch 78/100
26/26 [==============================] - 0s 4ms/step - c_loss: 2.4150 - c_acc: 0.6719 - p_loss: 0.6512 - p_acc: 0.7854 - val_p_loss: 0.6471 - val_p_acc: 0.7693
Epoch 79/100
26/26 [==============================] - 0s 3ms/step - c_loss: 2.3057 - c_acc: 0.6723 - p_loss: 0.6538 - p_acc: 0.7023 - val_p_loss: 0.6487 - val_p_acc: 0.7034
Epoch 80/100
26/26 [==============================] - 0s 3ms/step - c_loss: 2.3322 - c_acc: 0.6731 - p_loss: 0.6553 - p_acc: 0.6385 - val_p_loss: 0.6467 - val_p_acc: 0.7732
Epoch 81/100
26/26 [==============================] - 0s 4ms/step - c_loss: 2.2771 - c_acc: 0.6727 - p_loss: 0.6528 - p_acc: 0.7131 - val_p_loss: 0.6463 - val_p_acc: 0.7854
Epoch 82/100
26/26 [==============================] - 0s 4ms/step - c_loss: 2.4103 - c_acc: 0.6700 - p_loss: 0.6512 - p_acc: 0.7485 - val_p_loss: 0.

In [ ]:
import tensorflow_datasets as tfds

print(train_dataset)

for t in train_dataset:
    print(t)

#print(tfds.as_numpy(train_dataset))

#for ds in tfds.as_numpy(train_dataset):
#    print(ds)

Model: "encoder"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 conv1d_8 (Conv1D)           (None, 6, 256)            512       
                                                                 
 conv1d_9 (Conv1D)           (None, 3, 256)            65792     
                                                                 
 conv1d_10 (Conv1D)          (None, 2, 256)            65792     
                                                                 
 conv1d_11 (Conv1D)          (None, 1, 256)            65792     
                                                                 
 flatten_2 (Flatten)         (None, 256)               0         
                                                                 
 dense_6 (Dense)             (None, 256)               65792     
                                                                 
Total params: 263,680
Trainable params: 263,680
Non-trainab

26/26 [==============================] - 0s 9ms/step - c_loss: 2.3489 - c_acc: 0.6646 - p_loss: 0.6944 - p_acc: 0.5000 - val_p_loss: 0.6894 - val_p_acc: 0.5326
Epoch 30/100
26/26 [==============================] - 0s 9ms/step - c_loss: 2.3372 - c_acc: 0.6752 - p_loss: 0.6952 - p_acc: 0.5554 - val_p_loss: 0.6892 - val_p_acc: 0.5149
Epoch 31/100
26/26 [==============================] - 0s 9ms/step - c_loss: 2.2892 - c_acc: 0.6696 - p_loss: 0.6976 - p_acc: 0.4854 - val_p_loss: 0.6891 - val_p_acc: 0.5149
Epoch 32/100
26/26 [==============================] - 0s 8ms/step - c_loss: 2.4868 - c_acc: 0.6744 - p_loss: 0.6962 - p_acc: 0.4908 - val_p_loss: 0.6891 - val_p_acc: 0.7510
Epoch 33/100
26/26 [==============================] - 0s 9ms/step - c_loss: 2.3364 - c_acc: 0.6788 - p_loss: 0.6965 - p_acc: 0.5415 - val_p_loss: 0.6890 - val_p_acc: 0.7816
Epoch 34/100
26/26 [==============================] - 0s 8ms/step - c_loss: 2.2931 - c_acc: 0.6767 - p_loss: 0.6975 - p_acc: 0.4838 - val_p_loss: 0.

26/26 [==============================] - 0s 8ms/step - c_loss: 1.6679 - c_acc: 0.6763 - p_loss: 0.7146 - p_acc: 0.4800 - val_p_loss: 0.6928 - val_p_acc: 0.4835
Epoch 77/100
26/26 [==============================] - 0s 8ms/step - c_loss: 1.7327 - c_acc: 0.6758 - p_loss: 0.7185 - p_acc: 0.4815 - val_p_loss: 0.6928 - val_p_acc: 0.4835
Epoch 78/100
26/26 [==============================] - 0s 9ms/step - c_loss: 1.5202 - c_acc: 0.6783 - p_loss: 0.7191 - p_acc: 0.4446 - val_p_loss: 0.6926 - val_p_acc: 0.5816
Epoch 79/100
26/26 [==============================] - 0s 9ms/step - c_loss: 1.6485 - c_acc: 0.6746 - p_loss: 0.7127 - p_acc: 0.4885 - val_p_loss: 0.6922 - val_p_acc: 0.5295
Epoch 80/100
26/26 [==============================] - 0s 9ms/step - c_loss: 1.6318 - c_acc: 0.6621 - p_loss: 0.7176 - p_acc: 0.4662 - val_p_loss: 0.6912 - val_p_acc: 0.5149
Epoch 81/100
26/26 [==============================] - 0s 8ms/step - c_loss: 1.5638 - c_acc: 0.6750 - p_loss: 0.7178 - p_acc: 0.4731 - val_p_loss: 0.

In [ ]:
# Supervised finetuning of the pretrained encoder
finetuning_model = keras.Sequential(
    [
        layers.Input(shape=(image_size, image_channels)),
        get_augmenter(**classification_augmentation),
        pretraining_model.encoder,
        layers.Dense(2),
    ],
    name="finetuning_model",
)
finetuning_model.compile(
    optimizer=keras.optimizers.Adam(),
    loss=keras.losses.SparseCategoricalCrossentropy(from_logits=True),
    metrics=[keras.metrics.SparseCategoricalAccuracy(name="acc")],
)

finetuning_history = finetuning_model.fit(
    labeled_train_dataset, epochs=num_epochs, validation_data=test_dataset
)
print(
    "Maximal validation accuracy: {:.2f}%".format(
        max(finetuning_history.history["val_acc"]) * 100
    )
)

In [ ]:
df_validation = pd.concat(
            pd.read_parquet(parquet_file)
            for parquet_file in parquet_dir_validation.glob('*.parquet')
         )

print(df_validation.shape)

df_validation = df_validation.drop_duplicates(subset='hex', keep="first")

df_hexes = df_validation[['hex']]

df_validation = df_validation[['B01','B02','B03','B04','B05','B06','B07','B08','B8A','B09','B11','B12']].astype('int')

predict_x = finetuning_model.predict(df_validation)
classes_x = np.argmax(predict_x,axis=1)
print(sum(classes_x==0),sum(classes_x==1))

df_classes = pd.DataFrame(classes_x, columns=['class'])

df_hexes = df_hexes.reset_index(drop=True)
df_classes = df_classes.reset_index(drop=True)

df_predict = pd.concat([df_hexes,df_classes], axis=1)

center = h3.h3_to_geo_boundary(h=df_predict.iloc[0]['hex'],geo_json=True)

m = folium.Map(location=(center[0][1], center[0][0]),
                tiles = 'https://server.arcgisonline.com/ArcGIS/rest/services/World_Imagery/MapServer/tile/{z}/{y}/{x}',
                attr = 'Esri',
                name = 'Esri Satellite',
                overlay = False,
                control = True)

for index, row in df_predict.iterrows():
    geometry = { "type" : "Polygon", "coordinates": [h3.h3_to_geo_boundary(h=row['hex'],geo_json=True)]}
    
    if row['class'] == 1:
        geo_j = folium.GeoJson(data=geometry, style_function=lambda x: {'fillColor': 'orange', 'color': 'green', 'weight': 0.5})
    else:
        geo_j = folium.GeoJson(data=geometry, style_function=lambda x: {'fillColor': 'blue', 'color': 'red', 'weight': 0.5})
    folium.Popup(str(row['hex'])).add_to(geo_j)
    geo_j.add_to(m)

m

# End of Notebook